In [1]:
import numpy as np 
import pandas as pd 
import os
from glob import glob
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from tqdm import tqdm
from sklearn.metrics import *
from sklearn.model_selection import *
from sklearn.preprocessing import *
from sklearn.linear_model import LinearRegression
import lightgbm as lgb
import xgboost as xgb
from sklearn.tree import *
from sklearn.ensemble import *

In [2]:
train = pd.read_csv('../data/train.csv')
test  = pd.read_csv('../data/test.csv')
sample_sub = pd.read_csv('../data/sample_submission.csv')
display(train)
display(test)
display(sample_sub)

stock_id  time_id    target
0              0        5  0.004136
1              0       11  0.001445
2              0       16  0.002168
3              0       31  0.002195
4              0       62  0.001747
...          ...      ...       ...
428927       126    32751  0.003461
428928       126    32753  0.003113
428929       126    32758  0.004070
428930       126    32763  0.003357
428931       126    32767  0.002090

[428932 rows x 3 columns]

stock_id  time_id row_id
0         0        4    0-4
1         0       32   0-32
2         0       34   0-34

row_id    target
0    0-4  0.003048
1   0-32  0.003048
2   0-34  0.003048

In [3]:
print('Different Unique Stocks IDS in training ',len(glob('../input/optiver-realized-volatility-prediction/book_train.parquet/*')),
      'Different Unique Stocks IDS in test ',len(glob('../input/optiver-realized-volatility-prediction/book_test.parquet/*'))
     )
print('Uniques in \n',train.nunique())
px.histogram(train.time_id)

Different Unique Stocks IDS in training  0 Different Unique Stocks IDS in test  0
Uniques in 
 stock_id       112
time_id       3830
target      414287
dtype: int64


In [4]:
def file_path_to_volatility(path,info=False):
    """We are losing much important when we try to find past record data as we only get 3 column stock_id time_id vol """
    part_data = []
    stock_id = path.split('/')[4].split('=')[1]
    sample_book = pd.read_parquet(path)
    sample_book['wap'] = (sample_book['bid_price1'] * sample_book['ask_size1'] + sample_book['ask_price1'] * sample_book['bid_size1']) / (sample_book['bid_size1']+ sample_book['ask_size1'])
    sample_book.dropna(inplace=True)
    for gid0,gid in tqdm(sample_book.groupby('time_id')):
        gid['log_return'] = gid['wap'].apply(lambda x:np.log(x)).diff()
        if info :
            print(f'Realized Volatiliy for time id {gid.time_id.iloc[0]} is ' ,np.sqrt(np.sum(gid['log_return'].reset_index(drop=True).drop(index = 0).apply(lambda x:x**2))))
        info_1 = np.array([stock_id,gid.time_id.iloc[0],np.sqrt(np.sum(gid['log_return'].reset_index(drop=True).drop(index = 0).apply(lambda x:x**2)))])
        info_2 = group_to_feature(gid)
#         print(describe_info.shape)
        info_1 = np.append(info_1,info_2) 
        part_data.append(info_1)
    return part_data
    
book_dir = glob('../data/book_train.parquet/*')
# PRE LOADING THIS FILE (ALREADY RAN AND SAVED IN INPUTS)
# train_data_vol = []
# for i in tqdm(book_dir):
#     train_data_vol.append(file_path_to_volatility(i))
# col_1 = ['stock_id','time_id','vol']
# col_2 = [f"desc_{i}" for i in range(63)]
# past_data = pd.concat([pd.DataFrame(i,columns=col_1+col_2) for i in train_data_vol])
# past_data.stock_id = past_data.stock_id.astype('int64')
past_data = pd.read_csv('../data/train.csv')
print(past_data.dtypes)
print(train.dtypes)
display(past_data)

stock_id      int64
time_id       int64
target      float64
dtype: object
stock_id      int64
time_id       int64
target      float64
dtype: object


stock_id  time_id    target
0              0        5  0.004136
1              0       11  0.001445
2              0       16  0.002168
3              0       31  0.002195
4              0       62  0.001747
...          ...      ...       ...
428927       126    32751  0.003461
428928       126    32753  0.003113
428929       126    32758  0.004070
428930       126    32763  0.003357
428931       126    32767  0.002090

[428932 rows x 3 columns]

In [5]:
def group_to_feature(df):
    """Capture Features """
    feature_sum = ['seconds_in_bucket','bid_price1', 'ask_price1','bid_price2', 'ask_price2', 'bid_size1', 'ask_size1', 'bid_size2','ask_size2']
    index = ['mean', 'std', 'min', '25%', '50%', '75%', 'max']
    val1 = df[feature_sum].describe().loc[index].values.reshape(-1)
#     val2 = np.sum(df[feature_sum]).values
    return val1

In [6]:
# METRICS
def rmspe(y_true, y_pred):
    return  (np.sqrt(np.mean(np.square((y_true - y_pred) / y_true))))
# print('root mean square percentage error'.upper(),rmspe(train_pred['target'],train_pred['vol']),
#      'root mean square error'.upper(),mean_squared_error(train_pred['target'],train_pred['vol']))
print(train.shape,past_data.shape)
display(pd.merge(train,past_data,on=['stock_id','time_id']))

(428932, 3) (428932, 3)


stock_id  time_id  target_x  target_y
0              0        5  0.004136  0.004136
1              0       11  0.001445  0.001445
2              0       16  0.002168  0.002168
3              0       31  0.002195  0.002195
4              0       62  0.001747  0.001747
...          ...      ...       ...       ...
428927       126    32751  0.003461  0.003461
428928       126    32753  0.003113  0.003113
428929       126    32758  0.004070  0.004070
428930       126    32763  0.003357  0.003357
428931       126    32767  0.002090  0.002090

[428932 rows x 4 columns]

In [7]:
def path_to_data(path):
    """ This return a merged dataframe of trades where the trades actually took place """
#     print(path)
    stock_id = path.split('/')[-1].split('=')[1]
    curr_book = pd.read_parquet(path)
    curr_trade = pd.read_parquet(path.replace('book','trade'))
    merged_data = pd.merge(curr_book,curr_trade,on=['time_id','seconds_in_bucket'])
    merged_data['stock_id'] = stock_id
#     print(curr_book.shape,curr_trade.shape,len(merged_data))
    if len(merged_data) ==0 :
        merged_data = curr_trade.merge(curr_book, how='cross',suffixes=['','_y'])
        merged_data['diff'] = abs(merged_data.seconds_in_bucket-merged_data.seconds_in_bucket_y)
        merged_data = pd.merge(merged_data.groupby(['time_id','seconds_in_bucket'])['diff'].min().reset_index(),merged_data,how="left")
        merged_data.drop(columns=['time_id_y','seconds_in_bucket_y','diff'],inplace=True)
        merged_data['stock_id'] = stock_id
    merged_data.dropna(inplace=True)
    merged_data.reset_index(drop=True)
    return merged_data

def read_all_files(path):
    """ Reads All file in the sub Folder (path / *) and read all parquets (trade/book) and picks only the first occurence based on Stock + Time
        Returns a list of all dataframes use concat to join them back ."""
    demo_all = []
    for i in tqdm(glob(os.path.join(path,'*'))):
        demo_merged = path_to_data(i)
        demo = demo_merged.groupby(['stock_id','time_id']).first().reset_index()
        demo.stock_id = demo.stock_id.astype('int64')
        demo_all.append(demo)
    return demo_all

def files_to_numbers(demo_all,vol_calculated,csv_path = '../input/optiver-realized-volatility-prediction/train.csv'):
    """ Takes in a List of DataFrame and Merges them with a CSV File and then with preprocessed data that we have where we calculate the Volatility
        at end of 10 min or bucket mark """
    csv_file = pd.read_csv(csv_path)
    demo = pd.concat(demo_all).reset_index(drop=True)
    demo_vol = pd.merge(csv_file,demo,on=['stock_id','time_id'])
    demo_vol_all_data = pd.merge(demo_vol,vol_calculated)
    return demo_vol_all_data

def ffill(data_df):
    data_df=data_df.set_index(['time_id', 'seconds_in_bucket'])
    data_df = data_df.reindex(pd.MultiIndex.from_product([data_df.index.levels[0], np.arange(0,600)], names = ['time_id', 'seconds_in_bucket']), method='ffill')
    return data_df.reset_index()

In [8]:
demo_all = read_all_files('../data/book_train.parquet')
data = files_to_numbers(demo_all,past_data,'../data/train.csv')
display(data)
# print(data.stock_id.value_counts())
# print(data.time_id.nunique())

100%|██████████| 112/112 [00:37<00:00,  2.99it/s]


stock_id  time_id    target  seconds_in_bucket  bid_price1  \
0              0        5  0.004136                 21    1.001422   
1              0       11  0.001445                  0    0.999473   
2              0       16  0.002168                 58    0.999641   
3              0       31  0.002195                  3    0.999815   
4              0       62  0.001747                 16    0.999790   
...          ...      ...       ...                ...         ...   
428908       126    32751  0.003461                 22    0.999673   
428909       126    32753  0.003113                  0    1.000620   
428910       126    32758  0.004070                 57    0.999852   
428911       126    32763  0.003357                  8    1.000757   
428912       126    32767  0.002090                 30    1.000154   

        ask_price1  bid_price2  ask_price2  bid_size1  ask_size1  bid_size2  \
0         1.002818    1.001370    1.002922          3         30          2   
1         1.000176    0.999423    1.000376        205        100         20   
2         1.000503    0.999210    1.000551        101         90        186   
3         1.000463    0.999769    1.000509        343        100          5   
4         1.000210    0.999557    1.000303        101         17          2   
...            ...         ...         ...        ...        ...        ...   
428908    1.000457    0.999641    1.000620        100         11          1   
428909    1.001275    1.000586    1.001310        120          3        100   
428910    1.000839    0.999803    1.001086        300          1        101   
428911    1.001350    1.000691    1.001613        100        100        100   
428912    1.000566    1.000103    1.001029        121        125        100   

        ask_size2     price  size  order_count  
0             100  1.002301   326           12  
1              30  0.999824     2            2  
2             300  1.000215     2            1  
3             142  1.000231    13            1  
4             100  1.000023     1            1  
...           ...       ...   ...          ...  
428908          6  0.999869     1            1  
428909        103  1.000713   238           16  
428910        100  1.000543   105            4  
428911          7  1.001114   397            7  
428912         87  1.000481   295            7  

[428913 rows x 15 columns]

In [9]:
feature = list(data.columns)
feature.remove('stock_id')
feature.remove('time_id')
feature.remove('target')
data_df = data.copy()
data_df.drop(columns=['stock_id','time_id'],inplace=True)
train_data,train_label = data_df[feature],data_df['target']
std_scaler = StandardScaler()
train_data_transform = std_scaler.fit_transform(train_data)


print('LINEAR REGRESSION')
lr = LinearRegression()
lr.fit(train_data_transform,train_label)
print(lr.score(train_data_transform,train_label),rmspe(lr.predict(train_data_transform),train_label))
# print('Mean Squared Error \t RMSPE METRIC(COMP)')
# print(mean_squared_error(lr.predict(train_data_transform),train_label),rmspe(lr.predict(train_data_transform),train_label))
# print(lr.predict(train_data_transform[:5]),train_label[:5].values)

print('LIGHT GBM')
lgbm = lgb.LGBMRegressor()
lgbm.fit(train_data_transform,train_label)
print('Mean Squared Error \t RMSPE METRIC(COMP)')
print(lgbm.score(train_data_transform,train_label),rmspe(lgbm.predict(train_data_transform),train_label))
print(lgbm.predict(train_data_transform[:5]),train_label[:5].values)

print('XGBOOST')
xgbreg =xgb.XGBRegressor()
xgbrreg = xgb.XGBRFRegressor()
xgbreg.fit(train_data_transform,train_label)
xgbrreg.fit(train_data_transform,train_label)
print('Mean Squared Error \t RMSPE METRIC(COMP)')
print(xgbreg.score(train_data_transform,train_label),rmspe(xgbreg.predict(train_data_transform),train_label))
print(xgbrreg.score(train_data_transform,train_label),rmspe(xgbrreg.predict(train_data_transform),train_label))

LINEAR REGRESSION
0.43110445704147593 5.4085012444212754
LIGHT GBM
Mean Squared Error 	 RMSPE METRIC(COMP)
0.5561145005568242 0.4341150623922099
[0.00531899 0.0035068  0.00344044 0.00292299 0.0031143 ] [0.00413577 0.00144459 0.00216819 0.00219526 0.00174722]
XGBOOST
Mean Squared Error 	 RMSPE METRIC(COMP)
0.6080407423167578 0.42049484107069424
0.4796212627465597 0.49652486311840466


In [21]:
train_x , val_x , train_y ,val_y = train_test_split(train_data,train_label,test_size=.1)
std_scaler = StandardScaler()
train_x_transform = std_scaler.fit_transform(train_x)
val_x_transform = std_scaler.transform(val_x)

In [28]:
train_x

seconds_in_bucket  bid_price1  ask_price1  bid_price2  ask_price2  \
155087                  0    1.001662    1.001698    1.001627    1.001733   
30620                   2    0.998848    0.999280    0.998800    0.999472   
147229                  9    0.999388    0.999633    0.999144    0.999878   
247633                  0    1.000068    1.000451    0.999955    1.000811   
309426                 47    0.998622    0.999956    0.998600    1.000289   
...                   ...         ...         ...         ...         ...   
424716                 18    0.998824    0.999005    0.998643    0.999186   
404246                  8    0.999683    0.999937    0.999556    1.000063   
63939                   4    0.999955    1.000435    0.999805    1.000525   
313660                  7    1.000288    1.000360    1.000216    1.000432   
377357                  0    0.998388    0.998695    0.998235    0.998849   

        bid_size1  ask_size1  bid_size2  ask_size2     price  size  \
155087        100        100        400        200  1.001627   100   
30620         200        100        200        100  0.998896    16   
147229        500       1000        600        900  0.999633   300   
247633        100         77         25        100  1.000360   322   
309426          1         27        160         13  0.999644     1   
...           ...        ...        ...        ...       ...   ...   
424716       1211        401       1906       1045  0.998824   800   
404246       1000        504       1100        900  0.999810   528   
63939          79          2         61         10  1.000195   100   
313660        669          4        500        915  1.000295   213   
377357        890       1115       2262       1010  0.998542   200   

        order_count  
155087            1  
30620             2  
147229            3  
247633           11  
309426            1  
...             ...  
424716            7  
404246            4  
63939             1  
313660            8  
377357            2  

[386021 rows x 12 columns]

[CV] END max_depth=11, max_features=log2, min_samples_split=10; total time=   1.6s
[CV] END max_depth=8, max_features=log2, min_samples_split=5; total time=   1.2s
[CV] END max_depth=11, max_features=log2, min_samples_split=10; total time=   1.6s
[CV] END max_depth=8, max_features=log2, min_samples_split=10; total time=   1.1s
[CV] END max_depth=11, max_features=log2, min_samples_split=10; total time=   1.6s
[CV] END max_depth=8, max_features=log2, min_samples_split=10; total time=   1.2s
[CV] END max_depth=5, max_features=log2, min_samples_split=10; total time=   0.8s
[CV] END max_depth=8, max_features=log2, min_samples_split=5; total time=   1.3s
[CV] END max_depth=3, max_features=log2, min_samples_split=10; total time=   0.4s
[CV] END max_depth=11, max_features=log2, min_samples_split=10; total time=   1.6s
[CV] END max_depth=8, max_features=log2, min_samples_split=10; total time=   1.2s
[CV] END max_depth=3, max_features=auto, min_samples_split=10; total time=   1.7s
[CV] END max_d

In [22]:
train_x_transform

array([[-5.41901679e-01,  7.69174366e-01,  5.17076324e-01, ...,
         6.27874394e-01, -1.34943668e-01, -5.56786147e-01],
       [-4.47643290e-01, -3.20933845e-01, -4.16939322e-01, ...,
        -4.37546232e-01, -1.77512702e-01, -3.85552331e-01],
       [-1.17738928e-01, -1.11638609e-01, -2.80561295e-01, ...,
        -1.50020776e-01, -3.35888236e-02, -2.14318514e-01],
       ...,
       [-3.53384901e-01,  1.07860520e-01,  2.94034191e-02, ...,
         6.92853950e-02, -1.34943668e-01, -5.56786147e-01],
       [-2.11997317e-01,  2.37002098e-01,  4.83817188e-04, ...,
         1.08394065e-01, -7.76781808e-02,  6.41850568e-01],
       [-5.41901679e-01, -4.98947915e-01, -6.42816149e-01, ...,
        -5.75705399e-01, -8.42662457e-02, -3.85552331e-01]])

In [15]:
import plotly.graph_objects as go
print('Decision Tree')
res_dtr = []
for i in range(15):
    dtr = DecisionTreeRegressor(max_depth=i+1)
    dtr.fit(train_x_transform,train_y)
    print(i+1,dtr.score(train_x_transform,train_y),rmspe(dtr.predict(train_x_transform),train_y),dtr.score(val_x_transform,val_y),rmspe(dtr.predict(val_x_transform),val_y))
    res_dtr.append([dtr.score(train_x_transform,train_y),rmspe(dtr.predict(train_x_transform),train_y),dtr.score(val_x_transform,val_y),rmspe(dtr.predict(val_x_transform),val_y)])
res_dtr = np.array(res_dtr)
graph_labels = ['Train Score','Train RMPSE','TEST SCORE','TEST RMPSE']
fig = go.Figure()
for i in range(res_dtr.shape[1]):
    fig.add_trace(go.Line(name=f"{graph_labels[i]}",y=res_dtr[:,i]))
fig.show()

Decision Tree
1 0.1122099886018294 0.7105837952925602 0.10933115607168109 0.7123899416569786
2 0.24490833175302884 0.6342822250462172 0.239394463986338 0.6363044142828191
3 0.3112274322089136 0.6052608566508443 0.3015432784693993 0.6111777252698878
4 0.35720320992838295 0.5768115086371346 0.34766879410575446 0.578248577667503
5 0.4094140758321846 0.5476079151404496 0.3988804187951822 0.549623692039304
6 0.4498890055719771 0.5237656665262895 0.4337308443276967 0.5262698666329418
7 0.48561653448078757 0.5024577720738196 0.46013732256096596 0.5060026948118079
8 0.5113322625740311 0.48626901227838426 0.470472801878299 0.49339453326909316
9 0.5351330822186853 0.47071327711821564 0.47876196520838055 0.48284435124602537
10 0.5565585366419532 0.45886593904373 0.47924614846030344 0.47831688287631025
11 0.5786483596876247 0.4472081986820325 0.4696624955848929 0.4763738678260515
12 0.6045061280058237 0.4357909995497835 0.45634744812240136 0.4754817793188135
13 0.6332696537354967 0.423458496535023

/home/roman/anaconda3/envs/dl/lib/python3.9/site-packages/plotly/graph_objs/_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




In [23]:
dtr_params ={
#     'criterion':['gini','entropy'],
    'max_depth':[3,5,8,11],
    'min_samples_split':[5,10],
#     'min_samples_leaf':[20,40,60,80],
    'max_features':['auto','log2'],
#     'max_leaf_nodes':[50,100]
}
dtr = DecisionTreeRegressor()
dtr_random = RandomizedSearchCV(dtr, dtr_params,verbose=2,n_jobs=-1)
best_param = dtr_random.fit(train_x_transform,train_y)
print(best_param.best_params_)
print(best_param.score(train_x_transform,train_y),rmspe(best_param.predict(train_x_transform),train_y),best_param.score(val_x_transform,val_y),rmspe(best_param.predict(val_x_transform),val_y))

Fitting 5 folds for each of 10 candidates, totalling 50 fits
{'min_samples_split': 10, 'max_features': 'auto', 'max_depth': 8}
0.5093867730275399 0.484912662890932 0.4804827182203688 0.4946290440456996


In [27]:
train_y

155087    0.001696
30620     0.003323
147229    0.002742
247633    0.002325
309426    0.003175
            ...   
424716    0.002005
404246    0.001869
63939     0.002441
313660    0.001270
377357    0.001845
Name: target, Length: 386021, dtype: float64

In [17]:
print('Random Forest Regressor')
res_forest = []
for i in range(10):
    rfr = DecisionTreeRegressor(max_depth=i+1)
    rfr.fit(train_x_transform,train_y)
    print(i+1,rfr.score(train_x_transform,train_y),rmspe(rfr.predict(train_x_transform),train_y),rfr.score(val_x_transform,val_y),rmspe(rfr.predict(val_x_transform),val_y))
    res_forest.append([rfr.score(train_x_transform,train_y),rmspe(rfr.predict(train_x_transform),train_y),rfr.score(val_x_transform,val_y),rmspe(rfr.predict(val_x_transform),val_y)])
res_forest = np.array(res_forest)
graph_labels = ['Train Score','Train RMPSE','TEST SCORE','TEST RMPSE']
fig = go.Figure()
for i in range(res_forest.shape[1]):
    fig.add_trace(go.Line(name=f"{graph_labels[i]}",y=res_forest[:,i]))
fig.show()

Random Forest Regressor
1 0.11220998860182929 0.7105837952925603 0.10933115607168098 0.7123899416569788
2 0.24490833175302895 0.6342822250462187 0.239394463986338 0.6363044142828207
3 0.3112274322089139 0.6052608566508447 0.3015432784693993 0.6111777252698881
4 0.35720320992838295 0.5768115086371316 0.34766879410575446 0.5782485776675
5 0.4094140758321846 0.5476079151404495 0.3988804187951822 0.5496236920393036
6 0.4498890055719771 0.5237656665262889 0.43373084432769693 0.5262698666329408
7 0.48561653448078757 0.5024577720738201 0.46013732256096596 0.5060026948118084
8 0.5113322625740311 0.48626901227838465 0.470472801878299 0.4933945332690933
9 0.5351330822186853 0.4707132771182158 0.4772234984310897 0.48267927695602925
10 0.5565585366419532 0.45886593904373 0.47408509987579306 0.4781621636743022


/home/roman/anaconda3/envs/dl/lib/python3.9/site-packages/plotly/graph_objs/_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




In [18]:
rfr = DecisionTreeRegressor(max_depth=5)
rfr.fit(train_x_transform,train_y)
print(rfr.score(train_x_transform,train_y),rmspe(rfr.predict(train_x_transform),train_y),rfr.score(val_x_transform,val_y),rmspe(rfr.predict(val_x_transform),val_y),np.sqrt(mean_squared_error(rfr.predict(train_x_transform),train_y)),np.sqrt(mean_squared_error(rfr.predict(val_x_transform),val_y)))

0.4094140758321845 0.5476079151404515 0.3988804187951822 0.5496236920393056 0.0022570807700895805 0.0022708713015366735


In [21]:
demo_all_pred = read_all_files('../data/book_test.parquet')

book_test_dir = glob('../data/book_test.parquet/*/*')
train_data_vol_pred = []
for i in tqdm(book_test_dir):
    train_data_vol_pred.append(file_path_to_volatility(i))
past_data_pred = pd.concat([pd.DataFrame(i,columns=past_data.columns) for i in train_data_vol_pred])
past_data_pred.stock_id = past_data_pred.stock_id.astype('int64')
past_data_pred.time_id = past_data_pred.time_id.astype('int64')

data_pred = files_to_numbers(demo_all_pred,past_data_pred,'../data/test.csv')
data_pred.dropna(inplace=True)
data_pred.reset_index(drop=True)
row_orderings = data_pred.row_id
data_pred.drop(columns='row_id',inplace=True)
data_pred = data_pred[feature]
pred = rfr.predict(std_scaler.transform(data_pred))
sub = pd.merge(sample_sub,pd.DataFrame({'row_id':row_orderings,'target':pred}),on='row_id',how='left',suffixes=['_old',''])[sample_sub.columns]
sub.target.fillna(0.003048022,inplace=True)
display(sub)
sub.to_csv('submission.csv',index=False)

  0%|                                                     | 0/1 [00:00<?, ?it/s]


IndexError: list index out of range

[CV] END max_depth=3, max_features=auto, min_samples_split=5; total time=   1.7s
[CV] END max_depth=11, max_features=log2, min_samples_split=10; total time=   1.4s
[CV] END max_depth=3, max_features=auto, min_samples_split=5; total time=   1.7s
[CV] END max_depth=11, max_features=log2, min_samples_split=10; total time=   1.4s
[CV] END max_depth=8, max_features=log2, min_samples_split=10; total time=   1.6s
[CV] END max_depth=11, max_features=log2, min_samples_split=10; total time=   1.6s
[CV] END max_depth=8, max_features=log2, min_samples_split=10; total time=   1.3s
[CV] END max_depth=11, max_features=log2, min_samples_split=10; total time=   1.6s
[CV] END max_depth=8, max_features=auto, min_samples_split=5; total time=   4.0s
[CV] END max_depth=8, max_features=auto, min_samples_split=5; total time=   4.1s
[CV] END max_depth=8, max_features=auto, min_samples_split=5; total time=   4.1s
[CV] END max_depth=8, max_features=auto, min_samples_split=5; total time=   4.2s
[CV] END max_depth